In [2]:
import wfdb
import matplotlib.pyplot as plt
import matplotlib 
import pandas as pd
import os
import json
import tqdm
import numpy as np
from torch.utils.data import Dataset, DataLoader
import torch

In [65]:
np.set_printoptions(threshold=np.inf)

In [3]:
pd.set_option("display.max_rows", None)

In [4]:
pd.set_option("display.max_columns", None)

path_data_csv = r"C:\Users\magra\Documents\HSD\5_Semester\Advances_AI\Project\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3"
# path_data_csv = r"C:\Users\magra\Documents\5_Semester\Advances_AI\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3"
ptbxl = pd.read_csv(os.path.join(path_data_csv, "ptbxl_database.csv"))
ptbxl.head()

ecg_id  patient_id   age  sex  height  weight  nurse  site     device  \
0       1     15709.0  56.0    1     NaN    63.0    2.0   0.0  CS-12   E   
1       2     13243.0  19.0    0     NaN    70.0    2.0   0.0  CS-12   E   
2       3     20372.0  37.0    1     NaN    69.0    2.0   0.0  CS-12   E   
3       4     17014.0  24.0    0     NaN    82.0    2.0   0.0  CS-12   E   
4       5     17448.0  19.0    1     NaN    70.0    2.0   0.0  CS-12   E   

        recording_date                                  report  \
0  1984-11-09 09:17:34  sinusrhythmus periphere niederspannung   
1  1984-11-14 12:55:37     sinusbradykardie sonst normales ekg   
2  1984-11-15 12:49:10              sinusrhythmus normales ekg   
3  1984-11-15 13:44:57              sinusrhythmus normales ekg   
4  1984-11-17 10:43:15              sinusrhythmus normales ekg   

                                  scp_codes heart_axis infarction_stadium1  \
0  {'NORM': 100.0, 'LVOLT': 0.0, 'SR': 0.0}        NaN                 NaN   
1              {'NORM': 80.0, 'SBRAD': 0.0}        NaN                 NaN   
2                {'NORM': 100.0, 'SR': 0.0}        NaN                 NaN   
3                {'NORM': 100.0, 'SR': 0.0}        NaN                 NaN   
4                {'NORM': 100.0, 'SR': 0.0}        NaN                 NaN   

  infarction_stadium2  validated_by  second_opinion  \
0                 NaN           NaN           False   
1                 NaN           NaN           False   
2                 NaN           NaN           False   
3                 NaN           NaN           False   
4                 NaN           NaN           False   

   initial_autogenerated_report  validated_by_human  baseline_drift  \
0                         False                True             NaN   
1                         False                True             NaN   
2                         False                True             NaN   
3                         False                True    , II,III,AVF   
4                         False                True   , III,AVR,AVF   

  static_noise burst_noise electrodes_problems extra_beats pacemaker  \
0    , I-V1,           NaN                 NaN         NaN       NaN   
1          NaN         NaN                 NaN         NaN       NaN   
2          NaN         NaN                 NaN         NaN       NaN   
3          NaN         NaN                 NaN         NaN       NaN   
4          NaN         NaN                 NaN         NaN       NaN   

   strat_fold                filename_lr                filename_hr  
0           3  records100/00000/00001_lr  records500/00000/00001_hr  
1           2  records100/00000/00002_lr  records500/00000/00002_hr  
2           5  records100/00000/00003_lr  records500/00000/00003_hr  
3           3  records100/00000/00004_lr  records500/00000/00004_hr  
4           4  records100/00000/00005_lr  records500/00000/00005_hr

In [5]:
scp_codes = pd.read_csv(os.path.join(path_data_csv, "scp_statements.csv"))
scp_codes.head()

Unnamed: 0                     description  diagnostic  form  rhythm  \
0        NDT  non-diagnostic T abnormalities         1.0   1.0     NaN   
1       NST_         non-specific ST changes         1.0   1.0     NaN   
2        DIG                digitalis-effect         1.0   1.0     NaN   
3      LNGQT                long QT-interval         1.0   1.0     NaN   
4       NORM                      normal ECG         1.0   NaN     NaN   

  diagnostic_class diagnostic_subclass  \
0             STTC                STTC   
1             STTC                NST_   
2             STTC                STTC   
3             STTC                STTC   
4             NORM                NORM   

                                  Statement Category  \
0                  other ST-T descriptive statements   
1  Basic roots for coding ST-T changes and abnorm...   
2                  other ST-T descriptive statements   
3                  other ST-T descriptive statements   
4                                    Normal/abnormal   

    SCP-ECG Statement Description  AHA code            aECG REFID CDISC Code  \
0  non-diagnostic T abnormalities       NaN                   NaN        NaN   
1         non-specific ST changes     145.0  MDC_ECG_RHY_STHILOST        NaN   
2       suggests digitalis-effect     205.0                   NaN        NaN   
3                long QT-interval     148.0                   NaN        NaN   
4                      normal ECG       1.0                   NaN        NaN   

  DICOM Code  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4    F-000B7

In [24]:
print(scp_codes["diagnostic_subclass"].unique())
print(scp_codes["diagnostic_class"].unique())
print(scp_codes["Unnamed: 0"].unique())
print(scp_codes.shape)


['STTC' 'NST_' 'NORM' 'IMI' 'AMI' 'LVH' 'LAFB/LPFB' 'ISC_' 'IRBBB' '_AVB'
 'IVCD' 'ISCA' 'CRBBB' 'CLBBB' 'LAO/LAE' 'ISCI' 'LMI' 'RVH' 'RAO/RAE'
 'WPW' 'ILBBB' 'SEHYP' 'PMI' nan]
['STTC' 'NORM' 'MI' 'HYP' 'CD' nan]
['NDT' 'NST_' 'DIG' 'LNGQT' 'NORM' 'IMI' 'ASMI' 'LVH' 'LAFB' 'ISC_'
 'IRBBB' '1AVB' 'IVCD' 'ISCAL' 'CRBBB' 'CLBBB' 'ILMI' 'LAO/LAE' 'AMI'
 'ALMI' 'ISCIN' 'INJAS' 'LMI' 'ISCIL' 'LPFB' 'ISCAS' 'INJAL' 'ISCLA' 'RVH'
 'ANEUR' 'RAO/RAE' 'EL' 'WPW' 'ILBBB' 'IPLMI' 'ISCAN' 'IPMI' 'SEHYP'
 'INJIN' 'INJLA' 'PMI' '3AVB' 'INJIL' '2AVB' 'ABQRS' 'PVC' 'STD_' 'VCLVH'
 'QWAVE' 'LOWT' 'NT_' 'PAC' 'LPR' 'INVT' 'LVOLT' 'HVOLT' 'TAB_' 'STE_'
 'PRC(S)' 'SR' 'AFIB' 'STACH' 'SARRH' 'SBRAD' 'PACE' 'SVARR' 'BIGU' 'AFLT'
 'SVTAC' 'PSVT' 'TRIGU']
(71, 13)


In [7]:
ptbxl_ann = ptbxl[["ecg_id", "patient_id", "scp_codes", "filename_lr"]]
ptbxl_ann.head()

ecg_id  patient_id                                 scp_codes  \
0       1     15709.0  {'NORM': 100.0, 'LVOLT': 0.0, 'SR': 0.0}   
1       2     13243.0              {'NORM': 80.0, 'SBRAD': 0.0}   
2       3     20372.0                {'NORM': 100.0, 'SR': 0.0}   
3       4     17014.0                {'NORM': 100.0, 'SR': 0.0}   
4       5     17448.0                {'NORM': 100.0, 'SR': 0.0}   

                 filename_lr  
0  records100/00000/00001_lr  
1  records100/00000/00002_lr  
2  records100/00000/00003_lr  
3  records100/00000/00004_lr  
4  records100/00000/00005_lr

In [8]:
intermediary_store=[]
import json
for index, row in ptbxl_ann.iterrows():
    row["scp_codes"] = row["scp_codes"].replace("'", '"')
    row["scp_codes"] = json.loads(row["scp_codes"])
    intermediary_store.append(row["scp_codes"])
intermediary_store

[{'NORM': 100.0, 'LVOLT': 0.0, 'SR': 0.0},
 {'NORM': 80.0, 'SBRAD': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'IMI': 35.0, 'ABQRS': 0.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 80.0, 'SARRH': 0.0},
 {'NORM': 80.0, 'SBRAD': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SARRH': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'AFLT': 100.0, 'ABQRS': 0.0, 'AFIB': 0.0},
 {'AFLT': 100.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'AFLT': 100.0, 'ABQRS': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NDT': 100.0, 'SR': 0.0},
 {'AFLT': 100.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'NST_': 100.0, 'DIG': 100.0, 'SR': 0.0},
 {'NORM': 80.0, 'SR': 0.0},
 {'NST_': 100.0, 'DIG': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'LVH': 100.0, 'SR': 0.0},
 {'NORM': 100.0, 'SR': 0.0},
 {'LPFB': 100.0, 'SR': 0.0},
 {'NORM': 100.0

In [9]:
ptbxl_ann["scp_codes"] = intermediary_store

C:\Users\magra\AppData\Local\Temp\ipykernel_3484\1873181576.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ptbxl_ann["scp_codes"] = intermediary_store


In [39]:
data_one_scp_code = []
for index, row in ptbxl_ann.iterrows():
    dictionary = row["scp_codes"]
    
    
    if isinstance(dictionary, dict):
        print(dictionary)
        # find key that corresponds to highest value
        max_key = max(dictionary, key = dictionary.get)
        print(max_key)
        # get value associated with max_key
        max_value = dictionary[max_key]

        if max_value >= 70:
            # first two columns stay the same
            ecg_id_value = row["ecg_id"]
            patient_id_value = row["patient_id"]
            filename_100 = row["filename_lr"]
            # add to list for storage
            data_one_scp_code.append([ecg_id_value, patient_id_value, max_key, max_value, filename_100])

data_one_scp_df = pd.DataFrame(data_one_scp_code, columns=["ecg_id", "patient_id", "max_key", "max_value", "filename_lr"])

{'NORM': 100.0, 'LVOLT': 0.0, 'SR': 0.0}
NORM
{'NORM': 80.0, 'SBRAD': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'IMI': 35.0, 'ABQRS': 0.0, 'SR': 0.0}
IMI
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 80.0, 'SARRH': 0.0}
NORM
{'NORM': 80.0, 'SBRAD': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SARRH': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'AFLT': 100.0, 'ABQRS': 0.0, 'AFIB': 0.0}
AFLT
{'AFLT': 100.0}
AFLT
{'NORM': 100.0, 'SR': 0.0}
NORM
{'AFLT': 100.0, 'ABQRS': 0.0}
AFLT
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NDT': 100.0, 'SR': 0.0}
NDT
{'AFLT': 100.0}
AFLT
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NORM': 100.0, 'SR': 0.0}
NORM
{'NST_': 100.0, 'DIG': 100.0, 'SR': 0.0}
NST_
{'NORM': 80.0, 'SR': 0.0}
NORM
{'NST_': 100.0, 'DIG': 100.0, 'SR': 0.0}
NST_
{'NORM': 100.0, 'SR': 0.0}
NORM
{'LVH': 100.0, '

In [40]:
data_one_scp_df
print(data_one_scp_df.head(5))


   ecg_id  patient_id max_key  max_value                filename_lr
0       1     15709.0    NORM      100.0  records100/00000/00001_lr
1       2     13243.0    NORM       80.0  records100/00000/00002_lr
2       3     20372.0    NORM      100.0  records100/00000/00003_lr
3       4     17014.0    NORM      100.0  records100/00000/00004_lr
4       5     17448.0    NORM      100.0  records100/00000/00005_lr


In [41]:
diagnostic_class = []
diagnostic_subclass = []
for i in data_one_scp_df["max_key"]:
    #print("i", i)
    diagnostic_class.append(scp_codes.loc[scp_codes["Unnamed: 0"] == i, "diagnostic_class"].values[0])
    diagnostic_subclass.append(scp_codes.loc[scp_codes["Unnamed: 0"] == i, "diagnostic_subclass"].values[0])
    

In [42]:
print(data_one_scp_df.shape)
print(len(diagnostic_class))
print(len(diagnostic_subclass))
print(set(diagnostic_class))

(19683, 5)
19683
19683
{nan, 'HYP', 'STTC', 'CD', 'NORM', 'MI'}


In [43]:
data_one_scp_df["diagnostic_class"] = diagnostic_class
data_one_scp_df["diagnostic_subclass"] = diagnostic_subclass

In [26]:
print(scp_codes.loc[scp_codes["Unnamed: 0"] == "AFLT"])

   Unnamed: 0     description  diagnostic  form  rhythm diagnostic_class  \
67       AFLT  atrial flutter         NaN   NaN     1.0              NaN   

   diagnostic_subclass                                 Statement Category  \
67                 NaN  Statements related to impulse formation (abnor...   

   SCP-ECG Statement Description  AHA code            aECG REFID CDISC Code  \
67                atrial flutter      51.0  MDC_ECG_RHY_ATR_FLUT        NaN   

   DICOM Code  
67        NaN  


In [44]:
data_one_scp_df[data_one_scp_df["diagnostic_class"].isnull()].shape 

(651, 7)

In [45]:
data_one_scp_df[data_one_scp_df["diagnostic_subclass"].isnull()].shape

(651, 7)

In [46]:
(data_one_scp_df["diagnostic_subclass"].isnull() == data_one_scp_df["diagnostic_class"].isnull()).unique

<bound method Series.unique of 0        True
1        True
2        True
3        True
4        True
5        True
6        True
7        True
8        True
9        True
10       True
11       True
12       True
13       True
14       True
15       True
16       True
17       True
18       True
19       True
20       True
21       True
22       True
23       True
24       True
25       True
26       True
27       True
28       True
29       True
30       True
31       True
32       True
33       True
34       True
35       True
36       True
37       True
38       True
39       True
40       True
41       True
42       True
43       True
44       True
45       True
46       True
47       True
48       True
49       True
50       True
51       True
52       True
53       True
54       True
55       True
56       True
57       True
58       True
59       True
60       True
61       True
62       True
63       True
64       True
65       True
66       True
67       True
68       True
69 

In [47]:
data_one_scp_df.shape

(19683, 7)

In [48]:
data_one_scp_df=data_one_scp_df.dropna()

In [49]:
data_one_scp_df.shape

(19032, 7)

In [53]:
data_one_scp_df.head(10)

ecg_id  patient_id max_key  max_value                filename_lr  \
0       1     15709.0    NORM      100.0  records100/00000/00001_lr   
1       2     13243.0    NORM       80.0  records100/00000/00002_lr   
2       3     20372.0    NORM      100.0  records100/00000/00003_lr   
3       4     17014.0    NORM      100.0  records100/00000/00004_lr   
4       5     17448.0    NORM      100.0  records100/00000/00005_lr   
5       6     19005.0    NORM      100.0  records100/00000/00006_lr   
6       7     16193.0    NORM      100.0  records100/00000/00007_lr   
7       9     18792.0    NORM      100.0  records100/00000/00009_lr   
8      10      9456.0    NORM      100.0  records100/00000/00010_lr   
9      11     11243.0    NORM       80.0  records100/00000/00011_lr   

  diagnostic_class diagnostic_subclass  
0             NORM                NORM  
1             NORM                NORM  
2             NORM                NORM  
3             NORM                NORM  
4             NORM                NORM  
5             NORM                NORM  
6             NORM                NORM  
7             NORM                NORM  
8             NORM                NORM  
9             NORM                NORM

In [58]:
data_one_scp_df["diagnostic_class_numerical"] = data_one_scp_df.loc[:, "diagnostic_class"]
data_one_scp_df.head(5)

ecg_id  patient_id max_key  max_value                filename_lr  \
0       1     15709.0    NORM      100.0  records100/00000/00001_lr   
1       2     13243.0    NORM       80.0  records100/00000/00002_lr   
2       3     20372.0    NORM      100.0  records100/00000/00003_lr   
3       4     17014.0    NORM      100.0  records100/00000/00004_lr   
4       5     17448.0    NORM      100.0  records100/00000/00005_lr   

  diagnostic_class diagnostic_subclass diagnostic_class_duplicate  \
0             NORM                NORM                       NORM   
1             NORM                NORM                       NORM   
2             NORM                NORM                       NORM   
3             NORM                NORM                       NORM   
4             NORM                NORM                       NORM   

  diagnostic_class_numerical  
0                       NORM  
1                       NORM  
2                       NORM  
3                       NORM  
4                       NORM

In [60]:
data_one_scp_df["diagnostic_class"].unique()

array(['NORM', 'STTC', 'HYP', 'CD', 'MI'], dtype=object)

In [62]:
data_one_scp_df.loc[data_one_scp_df["diagnostic_class_numerical"] == "NORM", "diagnostic_class_numerical"] = 0
data_one_scp_df.loc[data_one_scp_df["diagnostic_class_numerical"] == "HYP", "diagnostic_class_numerical"] = 1
data_one_scp_df.loc[data_one_scp_df["diagnostic_class_numerical"] == "STTC", "diagnostic_class_numerical"] = 2
data_one_scp_df.loc[data_one_scp_df["diagnostic_class_numerical"] == "CD", "diagnostic_class_numerical"] = 3
data_one_scp_df.loc[data_one_scp_df["diagnostic_class_numerical"] == "MI", "diagnostic_class_numerical"] = 4
data_one_scp_df.head(20)
#'HYP', 'STTC', 'CD', 'NORM', 'MI

ecg_id  patient_id max_key  max_value                filename_lr  \
0        1     15709.0    NORM      100.0  records100/00000/00001_lr   
1        2     13243.0    NORM       80.0  records100/00000/00002_lr   
2        3     20372.0    NORM      100.0  records100/00000/00003_lr   
3        4     17014.0    NORM      100.0  records100/00000/00004_lr   
4        5     17448.0    NORM      100.0  records100/00000/00005_lr   
5        6     19005.0    NORM      100.0  records100/00000/00006_lr   
6        7     16193.0    NORM      100.0  records100/00000/00007_lr   
7        9     18792.0    NORM      100.0  records100/00000/00009_lr   
8       10      9456.0    NORM      100.0  records100/00000/00010_lr   
9       11     11243.0    NORM       80.0  records100/00000/00011_lr   
10      12     11031.0    NORM       80.0  records100/00000/00012_lr   
11      13     19953.0    NORM      100.0  records100/00000/00013_lr   
12      14     12925.0    NORM      100.0  records100/00000/00014_lr   
13      15     13375.0    NORM      100.0  records100/00000/00015_lr   
14      16     10999.0    NORM      100.0  records100/00000/00016_lr   
17      19     11116.0    NORM      100.0  records100/00000/00019_lr   
19      21     17102.0    NORM      100.0  records100/00000/00021_lr   
20      22     20978.0     NDT      100.0  records100/00000/00022_lr   
22      24      9012.0    NORM      100.0  records100/00000/00024_lr   
23      25     10962.0    NORM      100.0  records100/00000/00025_lr   

   diagnostic_class diagnostic_subclass diagnostic_class_duplicate  \
0              NORM                NORM                       NORM   
1              NORM                NORM                       NORM   
2              NORM                NORM                       NORM   
3              NORM                NORM                       NORM   
4              NORM                NORM                       NORM   
5              NORM                NORM                       NORM   
6              NORM                NORM                       NORM   
7              NORM                NORM                       NORM   
8              NORM                NORM                       NORM   
9              NORM                NORM                       NORM   
10             NORM                NORM                       NORM   
11             NORM                NORM                       NORM   
12             NORM                NORM                       NORM   
13             NORM                NORM                       NORM   
14             NORM                NORM                       NORM   
17             NORM                NORM                       NORM   
19             NORM                NORM                       NORM   
20             STTC                STTC                       STTC   
22             NORM                NORM                       NORM   
23             NORM                NORM                       NORM   

   diagnostic_class_numerical  
0                           0  
1                           0  
2                           0  
3                           0  
4                           0  
5                           0  
6                           0  
7                           0  
8                           0  
9                           0  
10                          0  
11                          0  
12                          0  
13                          0  
14                          0  
17                          0  
19                          0  
20                          2  
22                          0  
23                          0

In [63]:
data_one_scp_df["diagnostic_class_numerical"].unique()

array([0, 2, 1, 3, 4], dtype=object)

In [66]:
prelim_featurevector = pd.DataFrame(data_one_scp_df).to_numpy()
print(prelim_featurevector)
print(type(prelim_featurevector))
print(prelim_featurevector.shape)

[[1 15709.0 'NORM' 100.0 'records100/00000/00001_lr' 'NORM' 'NORM' 'NORM'
  0]
 [2 13243.0 'NORM' 80.0 'records100/00000/00002_lr' 'NORM' 'NORM' 'NORM'
  0]
 [3 20372.0 'NORM' 100.0 'records100/00000/00003_lr' 'NORM' 'NORM' 'NORM'
  0]
 [4 17014.0 'NORM' 100.0 'records100/00000/00004_lr' 'NORM' 'NORM' 'NORM'
  0]
 [5 17448.0 'NORM' 100.0 'records100/00000/00005_lr' 'NORM' 'NORM' 'NORM'
  0]
 [6 19005.0 'NORM' 100.0 'records100/00000/00006_lr' 'NORM' 'NORM' 'NORM'
  0]
 [7 16193.0 'NORM' 100.0 'records100/00000/00007_lr' 'NORM' 'NORM' 'NORM'
  0]
 [9 18792.0 'NORM' 100.0 'records100/00000/00009_lr' 'NORM' 'NORM' 'NORM'
  0]
 [10 9456.0 'NORM' 100.0 'records100/00000/00010_lr' 'NORM' 'NORM' 'NORM'
  0]
 [11 11243.0 'NORM' 80.0 'records100/00000/00011_lr' 'NORM' 'NORM' 'NORM'
  0]
 [12 11031.0 'NORM' 80.0 'records100/00000/00012_lr' 'NORM' 'NORM' 'NORM'
  0]
 [13 19953.0 'NORM' 100.0 'records100/00000/00013_lr' 'NORM' 'NORM'
  'NORM' 0]
 [14 12925.0 'NORM' 100.0 'records100/00000/00014_lr

In [67]:
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Device is {DEVICE}")

Device is cuda


In [77]:
class ECGDataset(torch.utils.data.Dataset):
  def __init__(self, seqlen):
    self.data = prelim_featurevector

    self.ecg = None
    self.labels = None
    self.seqlen = seqlen
    
    for idx in tqdm.tqdm(range(self.data.shape[0])):

        path_wfdb_100 = os.path.join(path_data_csv, prelim_featurevector[idx][4])
        record_100 = wfdb.rdrecord(path_wfdb_100)
        signal_physical_100 = record_100.p_signal  

        ecg = torch.Tensor(signal_physical_100).to(DEVICE).view(1,-1)
        #self.ecg.append(signal_physical_100)

        if self.ecg is None:
          self.ecg = ecg
        else:
          self.ecg = torch.concat((self.ecg, ecg), dim=0)

        #label = torch.Tensor(prelim_featurevector[idx][-1]).type(torch.long).to(DEVICE)
        label = torch.Tensor(prelim_featurevector[idx][8]).type(torch.long).to(DEVICE)
        #self.labels.append(prelim_featurevector[idx][2])

        if self.labels is None:
          self.labels = label
        else:
          self.labels = torch.concat((self.labels, label), dim=0)

    #self.ecg = torch.tensor(self.ecg)
    #self.labels = torch.tensor(self.labels)


  def __len__(self):
    return len(self.data) - self.seqlen
  
  def __getitem__(self, idx):
    return self.ecg[idx:(idx+self.seqlen)], self.labels[idx+self.seqlen]

In [78]:
dataset = ECGDataset(seqlen=4)

100%|██████████| 19032/19032 [02:30<00:00, 126.50it/s]


In [100]:
torch.set_printoptions(profile="full")
#print(dataset.labels)
print(dataset.labels.size())

torch.Size([29051])


In [96]:
for i in range (29):
    print(dataset[i][1])

tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(13517791088869376, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(13516760296718336, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')
tensor(0, device='cuda:0')


In [80]:
dataset[0][0].shape

torch.Size([4, 12000])

In [90]:
dataset[0][1]

tensor(0, device='cuda:0')

In [13]:
path_wfdb = r"C:\Users\magra\Documents\HSD\5_Semester\Advances_AI\Project\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3"
#path_wfdb = path_wfdb.replace('\\', "/")
path_wfdb

'C:\\Users\\magra\\Documents\\HSD\\5_Semester\\Advances_AI\\Project\\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3\\ptb-xl-a-large-publicly-available-electrocardiography-dataset-1.0.3'

In [10]:
wfdb_data = []
for i in tqdm.tqdm(range(prelim_featurevector.shape[0])):
    #print(prelim_featurevector[i][4])
    path_wfdb_100 = os.path.join(path_data_csv,  prelim_featurevector[i][4])
    #path_wfdb_100
    record_100 = wfdb.rdrecord(path_wfdb_100)
    signal_physical_100 = record_100.p_signal
    
    wfdb_data.append(signal_physical_100)
    #print(wfdb_data)

100%|██████████| 19683/19683 [08:27<00:00, 38.81it/s]


In [25]:
np.set_printoptions(threshold=np.inf)

In [29]:
wfdb_data

KeyboardInterrupt: 

In [30]:
wfdb_data[0][0][0]

-0.119

In [26]:
wfdb_data[0]

array([[-1.190e-01, -5.500e-02,  6.400e-02,  8.600e-02, -9.100e-02,
         4.000e-03, -6.900e-02, -3.100e-02,  0.000e+00, -2.600e-02,
        -3.900e-02, -7.900e-02],
       [-1.160e-01, -5.100e-02,  6.500e-02,  8.300e-02, -9.000e-02,
         6.000e-03, -6.400e-02, -3.600e-02, -3.000e-03, -3.100e-02,
        -3.400e-02, -7.400e-02],
       [-1.200e-01, -4.400e-02,  7.600e-02,  8.200e-02, -9.800e-02,
         1.600e-02, -5.800e-02, -3.400e-02, -1.000e-02, -2.800e-02,
        -2.900e-02, -6.900e-02],
       [-1.170e-01, -3.800e-02,  8.000e-02,  7.700e-02, -9.800e-02,
         2.100e-02, -5.000e-02, -3.000e-02, -1.500e-02, -2.300e-02,
        -2.200e-02, -6.400e-02],
       [-1.030e-01, -3.100e-02,  7.200e-02,  6.600e-02, -8.700e-02,
         2.100e-02, -4.500e-02, -2.700e-02, -2.000e-02, -1.900e-02,
        -1.800e-02, -5.800e-02],
       [-9.700e-02, -2.500e-02,  7.100e-02,  6.100e-02, -8.400e-02,
         2.300e-02, -3.600e-02, -2.500e-02, -9.000e-03, -1.400e-02,
        -1.200e-02,

In [16]:
type(wfdb_data[0])

numpy.ndarray

In [17]:
wfdb_data_np = np.array(wfdb_data)
print(wfdb_data_np[0].shape)


(1000, 12)


In [34]:
wfdb_data_np.shape[0]

19683

In [42]:
class DS():
    def __init__(self):
        pass

    def __len__(self):
        return self.wfdb_data_np.shape[0]
    
    def __getitem__(self, idx):
        return torch.Tensor(self.wfdb_data_np[idx]).to(DEVICE), 
                    torch.Tensor([prelim_featurevector_df[2].loc[idx]]).to(DEVICE).long()
    
ds = DS()
print(len(ds))

AttributeError: 'DS' object has no attribute 'wfdb_data_np'

In [ ]:
class WaveData(Dataset):
    def __init__(self):
        # data loading
        pass
    
    def __getitem__(self, index):
        # allows indexing
        pass

    def __len__(self):
        # len(dataset)
        pass

In [15]:
prelim_featurevector_df["wfdb"] = wfdb_data_np.tolist()

In [16]:
prelim_featurevector_df

0        1     2      3                          4  \
0          1  15709.0  NORM  100.0  records100/00000/00001_lr   
1          2  13243.0  NORM   80.0  records100/00000/00002_lr   
2          3  20372.0  NORM  100.0  records100/00000/00003_lr   
3          4  17014.0  NORM  100.0  records100/00000/00004_lr   
4          5  17448.0  NORM  100.0  records100/00000/00005_lr   
...      ...      ...   ...    ...                        ...   
19678  21832   7954.0  LAFB  100.0  records100/21000/21832_lr   
19679  21833  17180.0   NDT  100.0  records100/21000/21833_lr   
19680  21834  20703.0  NORM  100.0  records100/21000/21834_lr   
19681  21836   8873.0  NORM  100.0  records100/21000/21836_lr   
19682  21837  11744.0  NORM  100.0  records100/21000/21837_lr   

                                                    wfdb  
0      [[-0.119, -0.055, 0.064, 0.086, -0.091, 0.004,...  
1      [[0.004, 0.138, 0.134, -0.072, -0.065, 0.136, ...  
2      [[-0.029, -0.079, -0.049, 0.054, 0.011, -0.064...  
3      [[-0.054, -0.138, -0.083, 0.096, 0.015, -0.11,...  
4      [[-0.034, -0.574, -0.54, 0.304, 0.253, -0.556,...  
...                                                  ...  
19678  [[-0.076, -0.029, 0.046, 0.052, -0.061, 0.008,...  
19679  [[-0.052, -0.034, 0.018, 0.043, -0.034, -0.008...  
19680  [[-0.05, -0.013, 0.036, 0.031, -0.042, 0.011, ...  
19681  [[-0.057, -0.057, 0.0, 0.057, -0.028, -0.028, ...  
19682  [[-0.049, -0.025, 0.024, 0.037, -0.036, 0.0, 0...  

[19683 rows x 6 columns]

In [17]:
prelim_featurevector_wfdb_np = prelim_featurevector_df.to_numpy()

In [18]:
prelim_featurevector_wfdb_np.shape

(19683, 6)

In [19]:
prelim_featurevector_wfdb_np

array([[1, 15709.0, 'NORM', 100.0, 'records100/00000/00001_lr',
        list([[-0.119, -0.055, 0.064, 0.086, -0.091, 0.004, -0.069, -0.031, 0.0, -0.026, -0.039, -0.079], [-0.116, -0.051, 0.065, 0.083, -0.09, 0.006, -0.064, -0.036, -0.003, -0.031, -0.034, -0.074], [-0.12, -0.044, 0.076, 0.082, -0.098, 0.016, -0.058, -0.034, -0.01, -0.028, -0.029, -0.069], [-0.117, -0.038, 0.08, 0.077, -0.098, 0.021, -0.05, -0.03, -0.015, -0.023, -0.022, -0.064], [-0.103, -0.031, 0.072, 0.066, -0.087, 0.021, -0.045, -0.027, -0.02, -0.019, -0.018, -0.058], [-0.097, -0.025, 0.071, 0.061, -0.084, 0.023, -0.036, -0.025, -0.009, -0.014, -0.012, -0.052], [-0.119, -0.014, 0.106, 0.066, -0.112, 0.046, -0.029, -0.012, 0.005, -0.008, -0.007, -0.048], [-0.096, 0.008, 0.104, 0.044, -0.1, 0.056, -0.023, 0.003, 0.018, 0.002, -0.001, -0.041], [-0.048, 0.044, 0.092, 0.002, -0.07, 0.068, -0.015, 0.018, 0.021, 0.009, 0.005, -0.038], [-0.037, 0.045, 0.081, -0.004, -0.059, 0.063, -0.05, 0.009, 0.018, 0.022, 0.009, -0.033], 

In [76]:
#wfdb_data_np = wfdb_data_np.reshape(19683, -1)
prelim_featurevector_wfdb = np.concatenate((prelim_featurevector, wfdb_data_np[:,:,:].reshape((19683, -1))), axis=1)

In [74]:
prelim_featurevector_wfdb = np.hstack((prelim_featurevector, wfdb_data_np))

ValueError: all the input arrays must have same number of dimensions, but the array at index 0 has 2 dimension(s) and the array at index 1 has 3 dimension(s)

In [71]:
prelim_featurevector_wfdb.shape

(19683, 12005)

In [ ]:
print(path_wfdb)
path_wfdb_100 = os.path.join(path_wfdb,  prelim_featurevector[0][4])
path_wfdb_100

In [ ]:
record = wfdb.rdrecord(path_wfdb_100)
wfdb.plot_wfdb(record=record, title='Trial, ECG, Ending .hea') 
display(record.__dict__)

In [ ]:
signal_physical = record.p_signal
print(signal_physical)
signal_physical.shape